In [1]:
import vectorbtpro as vbt
import numpy as np
import pandas as pd

vbt.settings.set_theme('dark')
vbt.settings['plotting']['layout']['width'] = 800
vbt.settings['plotting']['layout']['height'] = 400

In [2]:
df = pd.read_csv('2ySOLdata1h.csv')
df['timestamp'] = pd.to_datetime(df['timestamp'], unit='s')
df.set_index('timestamp', inplace=True)


In [3]:
# Returns
df['ret1'] = df.Close.pct_change()


df['ret5'] = df.ret1.rolling(5).sum()
df['ret10'] = df.ret1.rolling(10).sum()
df['ret20'] = df.ret1.rolling(20).sum()
df['ret40'] = df.ret1.rolling(40).sum()

# Standard Deviation
df['std5'] = df.ret1.rolling(5).std()
df['std10'] = df.ret1.rolling(10).std()
df['std20'] = df.ret1.rolling(20).std()
df['std40'] = df.ret1.rolling(40).std()

df['retFut1'] = df.ret1.shift(-1)

In [4]:
df = df.dropna()
predictor_list = ['ret1', 'ret5', 'ret10', 'ret20',
                  'ret40', 'std5', 'std10', 'std20', 'std40', 'Volume']


In [5]:
data = vbt.Data.from_data(df)
data

In [6]:
open_price = data.get('Open')
high_price = data.get('High')
low_price = data.get('Low')
close_price = data.get('Close')

In [7]:
# vbt.IF.list_indicators("vbt") 

In [8]:
# vbt.phelp(vbt.SUPERTREND.run)

In [9]:
# adx = vbt.ADX.run(high_price, low_price, close_price, window=14)
# atr = vbt.ATR.run(high_price, low_price, close_price, window=14)
# bbands = vbt.BBANDS.run(close_price, window=14)
# rsi = vbt.RSI.run(close_price)
# sma = vbt.MA.run(close_price, window=20)
# strend = vbt.SUPERTREND.run(high_price, low_price, close_price, period=7, multiplier=3)


In [10]:
# data.data['symbol']['ADX'] = adx.adx
# data.data['symbol']['ATR'] = atr.atr
# data.data['symbol']['LBBAND'] = bbands.lower
# data.data['symbol']['UBBAND'] = bbands.upper
# data.data['symbol']['RSI'] = rsi.rsi
# data.data['symbol']['SMA'] = sma.ma
# data.data['symbol']['STREND'] = strend.trend

In [11]:

X = data.data['symbol'][predictor_list]
# print(X)

y = data.data['symbol']['retFut1']
# y

In [12]:
train_length = int(len(data.data['symbol'])*0.80)

X_train = X[:train_length]
X_test = X[train_length:]
y_train = y[:train_length]
y_test = y[train_length:]

In [13]:
# Regression tree model
from sklearn.tree import DecisionTreeRegressor
dtr = DecisionTreeRegressor(min_samples_leaf=400)

In [14]:
dtr.fit(X_train, y_train)

DecisionTreeRegressor(min_samples_leaf=400)

In [16]:
# import graphviz
# from sklearn import tree

# dot_data = tree.export_graphviz(dtr,
#                                 out_file=None,
#                                 filled=True,
#                                 feature_names=predictor_list)
# graphviz.Source(dot_data)

In [17]:
data.data['symbol']['predicted_signal'] = np.where(
    ((data.data['symbol']['ret20'] > 0.002) & (data.data['symbol']['std20'] > 0.01) & (data.data['symbol']['ret20'] <= 0.049) & (data.data['symbol']['ret40'] <= 0.031)), 1, 0)

In [19]:
# # Store the test dataset in new dataframe df_split
# df_split = data.data['symbol'][train_length:].copy()

# # Store the decision tree's predicted output to signal column of df_split dataframe
# df_split.loc[:, "signal"] = y_pred

In [20]:
signal = data.data['symbol']['predicted_signal']
entries = signal == 1
exits = signal == 0


In [28]:
pf = vbt.Portfolio.from_signals(
    close=data.data['symbol']['Close'],
    long_entries=entries, 
    long_exits=exits,
    size=100,
    size_type='value',
    init_cash='auto'
)

In [29]:
# import joblib
# def save_model(model, model_filename='trained_model.joblib'):
#     joblib.dump(model, model_filename)
#     print(f'Model saved as {model_filename}')
# save_model(clf)

In [30]:
pf.plot({"orders", "cum_returns"}, settings=dict(bm_returns=False)).show()

In [24]:
pf.stats()

Start                         2022-01-02 20:00:00+00:00
End                           2023-12-31 05:00:00+00:00
Period                                727 days 10:00:00
Start Value                                  101.110454
Min Value                                         100.0
Max Value                                    282.581201
End Value                                    276.875914
Total Return [%]                             173.835102
Benchmark Return [%]                         -41.838818
Total Time Exposure [%]                        4.908924
Max Gross Exposure [%]                            100.0
Max Drawdown [%]                               8.706626
Max Drawdown Duration                  85 days 12:00:00
Total Orders                                        650
Total Fees Paid                                     0.0
Total Trades                                        325
Win Rate [%]                                  58.153846
Best Trade [%]                                 9